In [1]:
import numpy as np
import xarray as xr
import matplotlib.pyplot as plt
import hvplot.xarray
import cartopy.crs as ccrs
from datetime import datetime, timedelta

## Load in data

In [2]:
dem = xr.open_dataarray('dem.nc', 
                        chunks={'x': 2188/4, 'y':3558/2}   # turning on dask seems to performance slightly.
                       )  
dem

<xarray.DataArray (y: 3558, x: 2188)>
dask.array<open_dataset-16e6d6e9ceb1515bc061c2c3d86c1794__xarray_dataarray_variable__, shape=(3558, 2188), dtype=float32, chunksize=(1779, 547), chunktype=numpy.ndarray>
Coordinates:
    band     int64 ...
  * y        (y) float64 4.395e+06 4.395e+06 4.395e+06 ... 4.128e+06 4.128e+06
  * x        (x) float64 7.892e+05 7.892e+05 7.893e+05 ... 9.532e+05 9.532e+05
Attributes:
    transform:      [ 7.50319927e+01  0.00000000e+00  7.89113000e+05  0.00000...
    crs:            +init=epsg:32140
    res:            [75.03199269 75.03199269]
    is_tiled:       1
    nodatavals:     nan
    scales:         1.0
    offsets:        0.0
    AREA_OR_POINT:  Area
    DataType:       Generic

## create (and save) a new dataset from numpy arrays

In [3]:
# extract values from DataArray
x = dem.x.values
y = dem.y.values
dem_values= dem.values

In [5]:
# create dataset based on numpy arrays
ds = xr.Dataset(
    {"dem": (["y", "x"], dem_values[::-1, :])},
    coords={"x": (["x",], x),
            "y": (["y",], y[::-1])},
)
ds

<xarray.Dataset>
Dimensions:  (x: 2188, y: 3558)
Coordinates:
  * x        (x) float64 7.892e+05 7.892e+05 7.893e+05 ... 9.532e+05 9.532e+05
  * y        (y) float64 4.128e+06 4.128e+06 4.128e+06 ... 4.395e+06 4.395e+06
Data variables:
    dem      (y, x) float32 55.757236 56.166676 ... 127.82575 126.395134

In [ ]:
# ds.to_netcdf('dem_ds.nc')

## Visualize the dataset using holoviews

In [6]:
ds.dem.hvplot.quadmesh(x='x', y='y', rasterize=True, crs=ccrs.epsg(32140), coastline=True)

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [x,y]   (dem)
      .Coastline.I :Feature   [Longitude,Latitude]

## An example of some analysis to do

Imagine we have this DEM, and are interested in inundation. We have hitorical sealevel records and we want to create a map of how often different regions experience flooding. 

To do this, let's first create a fictional timeseries of sealevel elevation.

In [18]:
# this is a random timeseries with values that approximately span the DEM range
# just to be sure we see something interesting
ssh = 5.0 * np.random.randn(1000) + 50.0 

start_date = datetime(1600, 1, 1)
time = np.array([start_date + timedelta(days=150*i) for i in range(len(ssh))])

The key to the analysis is to realize that we have three dimensions now; two spatial dimensions and one time dimension. Let's convert our ssh array into a DataArray for ease of use with the DEM DataArray

In [19]:
ds['ssh'] = xr.DataArray(ssh, coords={'time': time}, dims=['time'], name='ssh')
ds = ds.chunk(chunks={'x': 2188/4, 'y':3558/2, 'time':100})
ds

<xarray.Dataset>
Dimensions:  (time: 1000, x: 2188, y: 3558)
Coordinates:
  * x        (x) float64 7.892e+05 7.892e+05 7.893e+05 ... 9.532e+05 9.532e+05
  * y        (y) float64 4.128e+06 4.128e+06 4.128e+06 ... 4.395e+06 4.395e+06
  * time     (time) object 1600-01-01 1600-05-30 ... 2009-11-12 2010-04-11
Data variables:
    dem      (y, x) float32 dask.array<chunksize=(1779, 547), meta=np.ndarray>
    ssh      (time) float64 dask.array<chunksize=(100,), meta=np.ndarray>

Now, when we multiply the DEM by SSH, the coordinates are projected in the way that makes sense. It knows that space and time dimensions are different and creates a 3D array.

In [20]:
(ds.dem * ds.ssh) * ds.dem

<xarray.DataArray (y: 3558, x: 2188, time: 1000)>
dask.array<mul, shape=(3558, 2188, 1000), dtype=float64, chunksize=(1779, 547, 100), chunktype=numpy.ndarray>
Coordinates:
  * x        (x) float64 7.892e+05 7.892e+05 7.893e+05 ... 9.532e+05 9.532e+05
  * y        (y) float64 4.128e+06 4.128e+06 4.128e+06 ... 4.395e+06 4.395e+06
  * time     (time) object 1600-01-01 1600-05-30 ... 2009-11-12 2010-04-11

Now, we just need to do the math right...

In [21]:
%%time 
wet = (ds.dem < ds.ssh).sum(dim='time').compute()
wet

CPU times: user 21.6 s, sys: 685 ms, total: 22.3 s
Wall time: 3.66 s


<xarray.DataArray (y: 3558, x: 2188)>
array([[ 130,  111,  108, ..., 1000, 1000, 1000],
       [ 126,  111,   94, ..., 1000, 1000, 1000],
       [ 134,  127,   99, ..., 1000, 1000, 1000],
       ...,
       [   0,    0,    0, ...,    0,    0,    0],
       [   0,    0,    0, ...,    0,    0,    0],
       [   0,    0,    0, ...,    0,    0,    0]])
Coordinates:
  * x        (x) float64 7.892e+05 7.892e+05 7.893e+05 ... 9.532e+05 9.532e+05
  * y        (y) float64 4.128e+06 4.128e+06 4.128e+06 ... 4.395e+06 4.395e+06

In [22]:
(wet/wet.max()).hvplot.quadmesh(x='x', y='y', rasterize=True, 
                                clim=(0, 1),
                                crs=ccrs.epsg(32140), coastline=True)

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [x,y]   (value)
      .Coastline.I :Feature   [Longitude,Latitude]